In [1]:
import numpy as np
import matplotlib.pyplot as plt
import time
import csv

In [2]:
# nearest-neighbor interaction
def interaction(phase):
    return K*(np.sin(np.roll(phase,1,axis=0) - phase) 
            + np.sin(np.roll(phase,-1,axis=0) - phase) 
            + np.sin(np.roll(phase,1,axis=1) - phase)
            + np.sin(np.roll(phase,-1,axis=1) - phase))

In [11]:
Lx = 20 # system size = Lx x Ly
Ly = Lx
T = 0.002 # temperature
sigma = 0.005
K = 1 # strength of interaction
k_list = np.array([
    [(1,0),(0,1)],
    [(1,1),(1,-1)],
    [(2,0),(0,2)],
    [(2,1),(1,2),(2,-1),(1,-2)],
    [(2,2),(2,-2)],
    [(3,0),(0,3)],
    [(3,1),(1,3),(3,-1),(1,-3)]
])

dt = 0.01 # time increment
ini_steps = 2*int((Lx/2/np.pi)*(Lx/2/np.pi)/K/dt) # initialization steps = (relaxation time) * 2 / dt
n_steps = int(5e6) # simulation steps
t_run = n_steps * dt # simulation time

phase = np.zeros((Lx,Ly))
frequency = np.random.normal(0,sigma,(Lx,Ly)) # intrinsic freqency (Gaussian)

psi = np.zeros(n_steps,dtype=complex) # order parameter
modes_i = np.array([
    [0,0],
    [0,0],
    [0,0],
    [0,0,0,0],
    [0,0],
    [0,0],
    [0,0,0,0]
])
modes_f = np.array([
    [0,0],
    [0,0],
    [0,0],
    [0,0,0,0],
    [0,0],
    [0,0],
    [0,0,0,0]
])
data1 = np.zeros(len(k_list),dtype=complex) # |\theta_k| ^2 
err1 = np.zeros(len(k_list),dtype=complex) # |\theta_k| ^2 
data2 = np.zeros(len(k_list),dtype=complex) # \dot{\theta}_k \theta_{-k}
err2 = np.zeros(len(k_list),dtype=complex) # \dot{\theta}_k \theta_{-k}

In [12]:
aux = np.divmod(np.arange(Lx*Ly).reshape((Lx,Ly)),Ly)[0]

In [13]:
# let the system reach the steady state
start_time = time.time()

for t in range(ini_steps):
    phase += (( frequency + interaction(phase) ) * dt 
                + np.random.normal(0,np.sqrt(2*T*dt),(Lx,Ly)))
    
print("--- %s seconds ---" % (time.time() - start_time))

--- 0.16949820518493652 seconds ---


In [14]:
# relaxation
start_time = time.time()

with open('./Kuramoto_model_steady_state/Lx%d_Ly%d_T%.1e_sigma%.1e_K%.1e_t%.1e.csv'%(Lx,Ly,T,sigma,K,t_run),
          'w',newline='') as file:
    writer = csv.writer(file)
    
    for t in range(n_steps):
        noise = np.random.normal(0,np.sqrt(2*T*dt),(Lx,Ly))
        phase_tmp = phase + ( frequency + interaction(phase) ) * dt + noise
        phase_diff = ( frequency + (interaction(phase) + interaction(phase_tmp))/2 ) * dt + noise
        phase += phase_diff
    
        psi_i = np.average(np.exp(1j*(phase-phase_diff)))
        psi_f = np.average(np.exp(1j*phase))
        psi_angle_i = np.angle(psi_i)
        psi_angle_f = np.angle(psi_f)
        phi_i = np.angle(np.exp(1j*(phase-phase_diff)) * np.exp(-1j*psi_angle_i))
        phi_f = np.angle(np.exp(1j*(phase)) * np.exp(-1j*psi_angle_f))
        for k in range(len(k_list)):
            indctr = 0
            for kx, ky in k_list[k]:
                modes_i[k][indctr] = np.sum( phi_i * np.exp(2j*np.pi*aux*kx/Lx) * np.transpose(np.exp(2j*np.pi*aux*ky/Ly)) )
                modes_f[k][indctr] = np.sum( phi_f * np.exp(2j*np.pi*aux*kx/Lx) * np.transpose(np.exp(2j*np.pi*aux*ky/Ly)) )
                indctr += 1

        writer.writerow([modes_i[0][0],modes_i[0][1],
                         modes_i[1][0],modes_i[1][1],
                         modes_i[2][0],modes_i[2][1],
                         modes_i[3][0],modes_i[3][1],modes_i[3][2],modes_i[3][3],
                         modes_i[4][0],modes_i[4][1],
                         modes_i[5][0],modes_i[5][1],
                         modes_i[6][0],modes_i[6][1],modes_i[6][2],modes_i[6][3],
                         (modes_f[0][0]-modes_i[0][0])/dt,(modes_f[0][1]-modes_i[0][1])/dt,
                         (modes_f[1][0]-modes_i[1][0])/dt,(modes_f[1][1]-modes_i[1][1])/dt,
                         (modes_f[2][0]-modes_i[2][0])/dt,(modes_f[2][1]-modes_i[2][1])/dt,
                         (modes_f[3][0]-modes_i[3][0])/dt,(modes_f[3][1]-modes_i[3][1])/dt,
                         (modes_f[3][2]-modes_i[3][2])/dt,(modes_f[3][3]-modes_i[3][3])/dt,
                         (modes_f[4][0]-modes_i[4][0])/dt,(modes_f[4][1]-modes_i[4][1])/dt,
                         (modes_f[5][0]-modes_i[5][0])/dt,(modes_f[5][1]-modes_i[5][1])/dt,
                         (modes_f[6][0]-modes_i[6][0])/dt,(modes_f[6][1]-modes_i[6][1])/dt,
                         (modes_f[6][2]-modes_i[6][2])/dt,(modes_f[6][3]-modes_i[6][3])/dt])
        
print("--- %s seconds ---" % (time.time() - start_time))

--- 8712.894575119019 seconds ---
